# Singular Value Decomposition

This notebook introduces the `da.linalg.svd` algorithms for the Singular Value Decomposition

## Start Dask Client for Dashboard

Starting the Dask Client is optional.  It will provide a dashboard which 
is useful to gain insight on the computation.  

The link to the dashboard will become visible when you create the client below.  We recommend having it open on one side of your screen while using your notebook on the other side.  This can take some effort to arrange your windows, but seeing them both at the same is very useful when learning.

In [1]:
from dask.distributed import Client, progress
client = Client(processes=False, threads_per_worker=4,
                n_workers=1, memory_limit='2GB')
client

<Client: 'inproc://10.20.0.141/15651/1' processes=1 threads=4, memory=2.00 GB>

## Compute SVD of Tall-and-Skinny Matrix

For many applications the provided matrix has many more rows than columns.  In this case a specialized algorithm can be used.

In [2]:
import dask.array as da

X = da.random.random((200000, 100), chunks=(10000, 100)).persist()

In [3]:
import dask

u, s, v = da.linalg.svd(X)
dask.visualize(u, s, v)

In [4]:
v.compute()

array([[ 0.10014714,  0.10001325,  0.09986142, ...,  0.10016616,
         0.09998952,  0.0999612 ],
       [ 0.01055507, -0.02789387,  0.03655409, ...,  0.16256349,
         0.06197425, -0.05025026],
       [-0.08347246,  0.04703819,  0.09674253, ...,  0.14502578,
        -0.05955064, -0.12809822],
       ...,
       [-0.08931525, -0.02062538,  0.14749404, ...,  0.05210477,
        -0.0574863 ,  0.06762515],
       [ 0.03946339, -0.09547679,  0.11306267, ...,  0.02572594,
         0.09139388,  0.07127639],
       [-0.13925475,  0.07483741, -0.10641552, ...,  0.05044665,
        -0.11567845, -0.03631502]])

## Compute SVD of General Non-Skinny Matrix with Approximate algorithm

When there are also many chunks in columns then we use an approximate randomized algorithm to collect only a few of the singular values and vectors.

In [5]:
import dask.array as da

X = da.random.random((10000, 10000), chunks=(2000, 2000)).persist()

In [6]:
import dask

u, s, v = da.linalg.svd_compressed(X, k=5)
dask.visualize(u, s, v)

In [7]:
v.compute()

array([[ 9.86145847e-03,  1.00338188e-02,  1.00323877e-02, ...,
         1.00722288e-02,  1.00181713e-02,  1.00045389e-02],
       [ 1.87019237e-02,  1.74167933e-02, -3.01951764e-03, ...,
         1.01590869e-02,  4.81881126e-03,  4.68828289e-03],
       [-1.03277604e-02, -1.15655540e-03,  4.35014588e-03, ...,
         7.22587865e-05, -7.82342530e-03,  1.55968989e-02],
       [-5.93626070e-03, -1.59150198e-03, -1.84992576e-02, ...,
        -2.02802612e-02, -3.60231064e-04, -3.02100713e-03],
       [ 1.14716300e-02, -1.02914046e-02, -2.18258965e-02, ...,
        -2.24512563e-02,  1.61896062e-02,  3.23035241e-03]])